In [1]:
import numpy as np

import sys
sys.path.append("../")
from koopmanlib.dictionary import PsiNN

In [2]:
basis_function = PsiNN(layer_sizes=[100,100,100], n_psi_train=100)

In [3]:
from duffing_oscillator import duffing_oscillator
from scipy.integrate import solve_ivp

# Parameters
delta = 0.5
alpha = -1
beta = 1

# Sample N=1000 initial points, with uniform distribution [-2, 2].
N = 1000
np.random.seed(39)
sample_data_x0 = (np.random.rand(N, 2) * 4) - 2

tspan = [0, 2.5]
nstep = 11
data = np.zeros((N, 2, nstep))

t_eval = np.linspace(tspan[0], tspan[1], nstep)

for idx, x0 in enumerate(sample_data_x0):
    sol = solve_ivp(duffing_oscillator, tspan, x0, t_eval=t_eval, args=(delta, alpha, beta))
    data[idx, 0, :] = sol.y[0]
    data[idx, 1, :] = sol.y[1]

# Pairwise shifted data X and Y
X = data[:, :, :-1] # shape: (1000, 2, 10)
Y = data[:, :, 1:]
print(X.shape, type(X))
print(Y.shape, type(Y))

# Transpose and reshape the data.
X = np.transpose(X, (0, 2, 1)).reshape(N * (nstep-1), 2) # shape: (10000, 2)
Y = np.transpose(Y, (0, 2, 1)).reshape(N * (nstep-1), 2)
print(X.shape, type(X))
print(Y.shape, type(Y))

(1000, 2, 10) <class 'numpy.ndarray'>
(1000, 2, 10) <class 'numpy.ndarray'>
(10000, 2) <class 'numpy.ndarray'>
(10000, 2) <class 'numpy.ndarray'>


In [4]:
len_all = X.shape[0]
data_x_train = X[:int(0.7*len_all),:]
data_x_valid = X[int(0.7*len_all)+1:,:]

data_y_train = Y[:int(0.7*len_all),:]
data_y_valid = Y[int(0.7*len_all)+1:,:]

In [5]:
data_train = [data_x_train, data_y_train]
data_valid = [data_x_valid, data_y_valid]

In [6]:
from koopmanlib.solver_0 import KoopmanDLSolver # resDMD solver using regression
solver = KoopmanDLSolver(dic=basis_function,
                         target_dim=np.shape(data_train)[-1],
                         reg=0.1)

solver.build(data_train=data_train,
             data_valid=data_valid,
             epochs=3000,
             batch_size=5000,
             lr=1e-4,
             log_interval=10,
             lr_decay_factor=.8)

Epoch 1/2
2/2 [==============================] - 1s 247ms/step - loss: 1.7821e-04 - val_loss: 0.0014
Epoch 2/2
2/2 [==============================] - 0s 45ms/step - loss: 0.0012 - val_loss: 4.5300e-04
number of the outer loop: 0
Epoch 1/2
2/2 [==============================] - 0s 81ms/step - loss: 1.2019e-04 - val_loss: 5.7597e-04
Epoch 2/2
2/2 [==============================] - 0s 51ms/step - loss: 4.3323e-04 - val_loss: 4.5898e-05
number of the outer loop: 1
Epoch 1/2
2/2 [==============================] - 0s 95ms/step - loss: 6.6016e-05 - val_loss: 3.8332e-04
Epoch 2/2
2/2 [==============================] - 0s 55ms/step - loss: 3.1859e-04 - val_loss: 3.0476e-05
number of the outer loop: 2
Epoch 1/2
2/2 [==============================] - 0s 96ms/step - loss: 3.9494e-05 - val_loss: 2.2268e-04
Epoch 2/2
2/2 [==============================] - 0s 50ms/step - loss: 1.8486e-04 - val_loss: 3.2760e-05
number of the outer loop: 3
Epoch 1/2
2/2 [==============================] - 0s 97ms/step -

In [7]:
evalues = solver.eigenvalues.T
efuns = solver.eigenfunctions(X)
kpm_modes = solver.compute_mode().T
N_dict = np.shape(evalues)[0]

resDMD_DL_outputs0 = {
    'resDMD_DL_outputs':{
    'efuns': efuns,
    'evalues': evalues,
    'kpm_modes': kpm_modes,
    'N_dict':N_dict
    }
}

print(resDMD_DL_outputs0['resDMD_DL_outputs']['evalues'])
print(resDMD_DL_outputs0['resDMD_DL_outputs']['efuns'].shape)

[ 1.01455777e+00+0.00000000e+00j  9.99998627e-01+0.00000000e+00j
  8.41903129e-01+1.62344365e-01j  8.41903129e-01-1.62344365e-01j
  7.72305051e-01-3.80295813e-01j  7.72305051e-01+3.80295813e-01j
  6.77636415e-01-2.89899706e-01j  6.77636415e-01+2.89899706e-01j
  4.54261742e-01-5.24382968e-01j  4.54261742e-01+5.24382968e-01j
  2.46244235e-01+0.00000000e+00j  1.65727643e-01-6.95676314e-01j
  1.65727643e-01+6.95676314e-01j  9.75637852e-02+1.01273463e-01j
  9.75637852e-02-1.01273463e-01j  8.56709075e-02+0.00000000e+00j
  2.23255797e-02+0.00000000e+00j  1.16067862e-02+0.00000000e+00j
  9.27775776e-03-2.57328898e-03j  9.27775776e-03+2.57328898e-03j
  1.61748451e-03+0.00000000e+00j  8.48152019e-04+2.13419099e-04j
  8.48152019e-04-2.13419099e-04j  2.50989205e-04+3.38060271e-05j
  2.50989205e-04-3.38060271e-05j  7.03881188e-05-9.57476757e-05j
  7.03881188e-05+9.57476757e-05j  5.24414233e-05-4.05991438e-05j
  5.24414233e-05+4.05991438e-05j  7.21929127e-06+0.00000000e+00j
  6.27750841e-06+0.000000

In [8]:
from koopmanlib.solver_1 import KoopmanDLSolver # resDMD solver using regression
solver = KoopmanDLSolver(dic=basis_function,
                         target_dim=np.shape(data_train)[-1],
                         reg=0.1)

solver.build(data_train=data_train,
             data_valid=data_valid,
             epochs=3000,
             batch_size=5000,
             lr=1e-4,
             log_interval=10,
             lr_decay_factor=.8)

Epoch 1/2
2/2 [==============================] - 30s 5s/step - loss: 0.8119 - val_loss: 0.8130
Epoch 2/2
2/2 [==============================] - 1s 306ms/step - loss: 0.8178 - val_loss: 0.8148
number of the outer loop: 0
Epoch 1/2
2/2 [==============================] - 1s 345ms/step - loss: 0.8141 - val_loss: 0.8126
Epoch 2/2
2/2 [==============================] - 0s 297ms/step - loss: 0.8158 - val_loss: 0.8114
number of the outer loop: 1
Epoch 1/2
2/2 [==============================] - 1s 320ms/step - loss: 0.8131 - val_loss: 0.8096
Epoch 2/2
2/2 [==============================] - 0s 304ms/step - loss: 0.8037 - val_loss: 0.8104
number of the outer loop: 2
Epoch 1/2
2/2 [==============================] - 1s 321ms/step - loss: 0.8145 - val_loss: 0.8100
Epoch 2/2
2/2 [==============================] - 1s 292ms/step - loss: 0.8080 - val_loss: 0.8083
number of the outer loop: 3
Epoch 1/2
2/2 [==============================] - 1s 350ms/step - loss: 0.8073 - val_loss: 0.8123
Epoch 2/2
2/2 [==

In [9]:
evalues = solver.eigenvalues.T
efuns = solver.eigenfunctions(X)
kpm_modes = solver.compute_mode().T
N_dict = np.shape(evalues)[0]

resDMD_DL_outputs1 = {
    'resDMD_DL_outputs':{
    'efuns': efuns,
    'evalues': evalues,
    'kpm_modes': kpm_modes,
    'N_dict':N_dict
    }
}

print(resDMD_DL_outputs1['resDMD_DL_outputs']['evalues'])
print(resDMD_DL_outputs1['resDMD_DL_outputs']['efuns'].shape)

[ 1.01191727e+00+0.00000000e+00j  1.00000325e+00+0.00000000e+00j
  8.42366089e-01-1.57186464e-01j  8.42366089e-01+1.57186464e-01j
  8.31226400e-01-3.49003536e-01j  8.31226400e-01+3.49003536e-01j
  7.67595738e-01+3.26920230e-01j  7.67595738e-01-3.26920230e-01j
  7.26263588e-01+0.00000000e+00j  6.63140736e-01+2.85040753e-01j
  6.63140736e-01-2.85040753e-01j  5.09208158e-01-5.22309963e-01j
  5.09208158e-01+5.22309963e-01j  4.88447309e-01+0.00000000e+00j
  2.39730572e-01+2.69849241e-01j  2.39730572e-01-2.69849241e-01j
  1.86147172e-01+0.00000000e+00j  1.65999361e-01+6.93771912e-01j
  1.65999361e-01-6.93771912e-01j  7.42902831e-02+2.47398161e-02j
  7.42902831e-02-2.47398161e-02j  7.12961116e-02+5.31714000e-02j
  7.12961116e-02-5.31714000e-02j  2.28835165e-02+2.95402363e-03j
  2.28835165e-02-2.95402363e-03j  6.33170807e-03+0.00000000e+00j
  4.86353601e-03+0.00000000e+00j  2.34207766e-03+0.00000000e+00j
  2.13251752e-03+0.00000000e+00j  6.63969171e-04-8.57251670e-03j
  6.63969171e-04+8.572516

In [10]:
from koopmanlib.solver_2 import KoopmanDLSolver # resDMD solver using regression
solver = KoopmanDLSolver(dic=basis_function,
                         target_dim=np.shape(data_train)[-1],
                         reg=0.1)

solver.build(data_train=data_train,
             data_valid=data_valid,
             epochs=3000,
             batch_size=5000,
             lr=1e-4,
             log_interval=10,
             lr_decay_factor=.8)

Epoch 1/2
2/2 [==============================] - 2s 582ms/step - loss: 553609.6339 - val_loss: 427488.7500
Epoch 2/2
2/2 [==============================] - 1s 431ms/step - loss: 517620.5179 - val_loss: 404232.9688
number of the outer loop: 0
Epoch 1/2
2/2 [==============================] - 1s 465ms/step - loss: 494553.6518 - val_loss: 385225.5938
Epoch 2/2
2/2 [==============================] - 1s 461ms/step - loss: 471837.2232 - val_loss: 368665.2188
number of the outer loop: 1
Epoch 1/2
2/2 [==============================] - 1s 491ms/step - loss: 457832.8839 - val_loss: 353591.0938
Epoch 2/2
2/2 [==============================] - 1s 470ms/step - loss: 435815.2188 - val_loss: 339553.1875
number of the outer loop: 2
Epoch 1/2
2/2 [==============================] - 1s 458ms/step - loss: 421335.5536 - val_loss: 326445.1875
Epoch 2/2
2/2 [==============================] - 1s 468ms/step - loss: 406195.9821 - val_loss: 314067.8125
number of the outer loop: 3
Epoch 1/2
2/2 [=================

In [11]:
evalues = solver.eigenvalues.T
efuns = solver.eigenfunctions(X)
kpm_modes = solver.compute_mode().T
N_dict = np.shape(evalues)[0]

resDMD_DL_outputs2 = {
    'resDMD_DL_outputs':{
    'efuns': efuns,
    'evalues': evalues,
    'kpm_modes': kpm_modes,
    'N_dict':N_dict
    }
}

print(resDMD_DL_outputs2['resDMD_DL_outputs']['evalues'])
print(resDMD_DL_outputs2['resDMD_DL_outputs']['efuns'].shape)

[ 1.00005433e+00+0.00000000e+00j  9.80070494e-01+0.00000000e+00j
  7.98140201e-01+0.00000000e+00j  7.91791916e-01-2.08637320e-01j
  7.91791916e-01+2.08637320e-01j  7.70807355e-01+0.00000000e+00j
  7.46504879e-01+3.83675924e-01j  7.46504879e-01-3.83675924e-01j
  5.93963238e-01+5.29434669e-01j  5.93963238e-01-5.29434669e-01j
  2.22146287e-01+1.18661388e-01j  2.22146287e-01-1.18661388e-01j
  1.90932552e-01+0.00000000e+00j  1.27746675e-01+8.83244713e-02j
  1.27746675e-01-8.83244713e-02j  7.84128404e-02+6.63887537e-02j
  7.84128404e-02-6.63887537e-02j  1.95908522e-02+4.06472076e-01j
  1.95908522e-02-4.06472076e-01j  1.85564020e-02+0.00000000e+00j
  9.47439047e-03+0.00000000e+00j  2.09044554e-03+0.00000000e+00j
  2.16571500e-04+5.61815945e-04j  2.16571500e-04-5.61815945e-04j
  1.46514318e-04+1.70253927e-04j  1.46514318e-04-1.70253927e-04j
  1.36825742e-04+2.59890932e-04j  1.36825742e-04-2.59890932e-04j
  6.49046358e-05-3.29328027e-05j  6.49046358e-05+3.29328027e-05j
  2.79725596e-05-2.620658

In [12]:
from koopmanlib.solver_3 import KoopmanDLSolver # resDMD solver using regression
solver = KoopmanDLSolver(dic=basis_function,
                         target_dim=np.shape(data_train)[-1],
                         reg=0.1)

solver.build(data_train=data_train,
             data_valid=data_valid,
             epochs=3000,
             batch_size=5000,
             lr=1e-4,
             log_interval=10,
             lr_decay_factor=.8)

Epoch 1/2
2/2 [==============================] - 1s 282ms/step - loss: 9.2336e-05 - val_loss: 0.0012
Epoch 2/2
2/2 [==============================] - 0s 129ms/step - loss: 9.2945e-04 - val_loss: 4.0859e-04
number of the outer loop: 0
Epoch 1/2
2/2 [==============================] - 0s 155ms/step - loss: 1.4683e-04 - val_loss: 5.8703e-04
Epoch 2/2
2/2 [==============================] - 0s 122ms/step - loss: 4.5367e-04 - val_loss: 1.3050e-04
number of the outer loop: 1
Epoch 1/2
2/2 [==============================] - 0s 150ms/step - loss: 6.0960e-05 - val_loss: 3.7058e-04
Epoch 2/2
2/2 [==============================] - 0s 115ms/step - loss: 3.1253e-04 - val_loss: 3.7725e-05
number of the outer loop: 2
Epoch 1/2
2/2 [==============================] - 0s 135ms/step - loss: 5.9141e-05 - val_loss: 2.6921e-04
Epoch 2/2
2/2 [==============================] - 0s 127ms/step - loss: 2.1041e-04 - val_loss: 5.0270e-05
number of the outer loop: 3
Epoch 1/2
2/2 [==============================] - 0s 

In [13]:
evalues = solver.eigenvalues.T
efuns = solver.eigenfunctions(X)
kpm_modes = solver.compute_mode().T
N_dict = np.shape(evalues)[0]

resDMD_DL_outputs3 = {
    'resDMD_DL_outputs':{
    'efuns': efuns,
    'evalues': evalues,
    'kpm_modes': kpm_modes,
    'N_dict':N_dict
    }
}

print(resDMD_DL_outputs3['resDMD_DL_outputs']['evalues'])
print(resDMD_DL_outputs3['resDMD_DL_outputs']['efuns'].shape)

[ 1.00005657e+00+0.00000000e+00j  9.89167725e-01+0.00000000e+00j
  8.04742122e-01-2.12583840e-01j  8.04742122e-01+2.12583840e-01j
  7.68687230e-01+3.47253030e-01j  7.68687230e-01-3.47253030e-01j
  7.40819901e-01+0.00000000e+00j  6.09942797e-01+4.82469793e-01j
  6.09942797e-01-4.82469793e-01j  6.07994633e-01+1.04113212e-01j
  6.07994633e-01-1.04113212e-01j  3.09322590e-01-1.67972832e-01j
  3.09322590e-01+1.67972832e-01j  1.16357160e-01-4.08184654e-02j
  1.16357160e-01+4.08184654e-02j  7.03493647e-02+4.65297710e-01j
  7.03493647e-02-4.65297710e-01j  5.90434962e-02+0.00000000e+00j
  3.26480080e-02+0.00000000e+00j  9.04240795e-03+0.00000000e+00j
  7.94241265e-03-4.70220795e-03j  7.94241265e-03+4.70220795e-03j
  4.03431359e-03+0.00000000e+00j  8.06515414e-04-1.68314647e-03j
  8.06515414e-04+1.68314647e-03j  6.65348430e-04+8.36802976e-04j
  6.65348430e-04-8.36802976e-04j  2.37946891e-04-2.41630786e-04j
  2.37946891e-04+2.41630786e-04j  2.00189441e-04+0.00000000e+00j
  4.74647995e-05+1.405814

In [14]:
from koopmanlib.solver_4 import KoopmanDLSolver # resDMD solver using regression
solver = KoopmanDLSolver(dic=basis_function,
                         target_dim=np.shape(data_train)[-1],
                         reg=0.1)

solver.build(data_train=data_train,
             data_valid=data_valid,
             epochs=3000,
             batch_size=5000,
             lr=1e-6,
             log_interval=10,
             lr_decay_factor=.8)

Epoch 1/2
2/2 [==============================] - 1s 335ms/step - loss: 0.4148 - val_loss: 1.2940
Epoch 2/2
2/2 [==============================] - 0s 144ms/step - loss: 0.2163 - val_loss: 1.2025
number of the outer loop: 0
Epoch 1/2
2/2 [==============================] - 0s 161ms/step - loss: 2.4425 - val_loss: 1.0667
Epoch 2/2
2/2 [==============================] - 0s 140ms/step - loss: 0.7472 - val_loss: 0.6839
number of the outer loop: 1
Epoch 1/2
2/2 [==============================] - 0s 177ms/step - loss: 1.4605 - val_loss: 1.0294
Epoch 2/2
2/2 [==============================] - 0s 134ms/step - loss: 1.1526 - val_loss: 0.9864
number of the outer loop: 2
Epoch 1/2
2/2 [==============================] - 0s 164ms/step - loss: 1.3785 - val_loss: 0.9542
Epoch 2/2
2/2 [==============================] - 0s 149ms/step - loss: 1.6092 - val_loss: 1.1650
number of the outer loop: 3
Epoch 1/2
2/2 [==============================] - 0s 174ms/step - loss: 2.0915 - val_loss: 0.9429
Epoch 2/2
2/2 [

In [15]:
evalues = solver.eigenvalues.T
efuns = solver.eigenfunctions(X)
kpm_modes = solver.compute_mode().T
N_dict = np.shape(evalues)[0]

resDMD_DL_outputs4 = {
    'resDMD_DL_outputs':{
    'efuns': efuns,
    'evalues': evalues,
    'kpm_modes': kpm_modes,
    'N_dict':N_dict
    }
}

print(resDMD_DL_outputs4['resDMD_DL_outputs']['evalues'])
print(resDMD_DL_outputs4['resDMD_DL_outputs']['efuns'].shape)

[ 1.00005676e+00+0.00000000e+00j  9.89224943e-01+0.00000000e+00j
  8.04917747e-01-2.12435327e-01j  8.04917747e-01+2.12435327e-01j
  7.68778692e-01-3.47034247e-01j  7.68778692e-01+3.47034247e-01j
  7.40841111e-01+0.00000000e+00j  6.09965618e-01-4.82603300e-01j
  6.09965618e-01+4.82603300e-01j  6.08323948e-01-1.06788545e-01j
  6.08323948e-01+1.06788545e-01j  3.09196485e-01-1.67646067e-01j
  3.09196485e-01+1.67646067e-01j  1.16876861e-01+4.05693759e-02j
  1.16876861e-01-4.05693759e-02j  7.00984128e-02+4.65850285e-01j
  7.00984128e-02-4.65850285e-01j  5.91398495e-02+0.00000000e+00j
  3.25771787e-02+0.00000000e+00j  9.04257594e-03+0.00000000e+00j
  7.90483257e-03-4.72443779e-03j  7.90483257e-03+4.72443779e-03j
  4.05362719e-03+0.00000000e+00j  8.01901617e-04+1.69520565e-03j
  8.01901617e-04-1.69520565e-03j  6.66843446e-04+8.39770188e-04j
  6.66843446e-04-8.39770188e-04j  2.39107141e-04-2.42365463e-04j
  2.39107141e-04+2.42365463e-04j  1.95411503e-04+0.00000000e+00j
  4.79405224e-05-1.404009